In [ ]:
import numpy as np
import seaborn as sns
import pandas as pd 
import matplotlib.pyplot as plt
import scipy.stats as stats
from statannot import add_stat_annotation
import scipy
import statsmodels
import statsmodels.stats.multitest
import matplotlib.lines as mlines
import ptitprince as pt

# https://matplotlib.org/stable/gallery/color/named_colors.html

In [ ]:
sns.set_style("whitegrid")
sns.set_context('talk') 

colors = ["teal", "mediumpurple", "plum", "indianred", "darkorange"]
classes_palette = sns.color_palette(colors)
sns.set_palette(classes_palette)

In [ ]:
f_path   = '.../markers'

In [ ]:
# Read .csv for all conditions
df_cm3v  =  pd.read_csv(f_path+'/ns_primate_markers_cm_3v_results.csv', 
                        sep=';',header=0,na_values="NaN")

df_cm5v  =  pd.read_csv(f_path+'/ns_primate_markers_cm_5v_results.csv', 
                        sep=';',header=0,na_values="NaN")

df_vl3v  =  pd.read_csv(f_path+'/ns_primate_markers_vl_3v_results.csv', 
                        sep=';',header=0,na_values="NaN")

df_vl5v  =  pd.read_csv(f_path+'/ns_primate_markers_vl_5v_results.csv', 
                        sep=';',header=0,na_values="NaN")

df_anest = pd.read_csv(f_path+'/ns_primate_markers_anest_results.csv', 
                        sep=';',header=0,na_values="NaN")

In [ ]:
# Add a stim_cond column to the dfs
cm3v_num_rows = df_cm3v.shape[0]
cm3v_stim_cond_list = cm3v_num_rows * ['cm3v']
df_cm3v['stim_cond'] = cm3v_stim_cond_list

cm5v_num_rows = df_cm5v.shape[0]
cm5v_stim_cond_list = cm5v_num_rows * ['cm5v']
df_cm5v['stim_cond'] = cm5v_stim_cond_list

vl3v_num_rows = df_vl3v.shape[0]
vl3v_stim_cond_list = vl3v_num_rows * ['vl3v']
df_vl3v['stim_cond'] = vl3v_stim_cond_list

vl5v_num_rows = df_vl5v.shape[0]
vl5v_stim_cond_list = vl5v_num_rows * ['vl5v']
df_vl5v['stim_cond'] = vl5v_stim_cond_list

anest_num_rows = df_anest.shape[0]
anest_stim_cond_list = anest_num_rows * ['anest']
df_anest['stim_cond'] = anest_stim_cond_list

In [ ]:
# Join the 4 dfs
df = df_cm3v.copy()
df_all = df.append([df_cm5v, df_vl3v, df_vl5v, df_anest])

In [ ]:
df_all.stim_cond.value_counts()

In [ ]:
order = ['anest', 'vl3v', 'vl5v', 'cm3v', 'cm5v']
order_names = ['Anesthesia', 'VL 3V', 'VL 5V', 'CM 3V', 'CM 5V']  

# All markers
Plotting drafts

In [ ]:
all_markers = df_all.marker.unique()

for mark in all_markers:
    print('Calculating marker : {}'.format(mark))
    df = df_all[df_all.marker == mark]

    f, ax = plt.subplots(figsize=(8, 6))
    ax=pt.RainCloud(x = "stim_cond", y = "avg_value", data = df, palette = classes_palette, bw = 0.3,
                    width_viol = .7, width_box = 0.1, ax = ax, orient = "v", 
                    move = .2, point_size=5, 
                    order=order) 
    test_pairs = [('cm3v', 'cm5v'), ('cm3v', 'vl3v'), ('cm3v', 'vl5v'), ('cm3v', 'anest'), 
                ('cm5v', 'vl3v'), ('cm5v', 'vl5v'), ('cm5v', 'anest'), 
                ('vl3v', 'vl5v'), ('vl3v', 'anest'), 
                ('vl5v', 'anest')]
    ax2, test_results = add_stat_annotation(ax, data=df, x="avg_value", y="stim_cond", order=order, 
                                    box_pairs=test_pairs, comparisons_correction=None,
                                    test='Mann-Whitney', text_format='star',fontsize=11,
                                    loc='outside', verbose=2, 
                                    line_offset_to_box=0.05, line_offset=0.01, line_height=0.02, text_offset=1);

    sns.despine(bottom=True, left=True)
    ax.set_title('Marker : {}'.format(mark), y= 0.93, fontsize=14)  
    plt.ylabel("Average value per recording of a marker", fontsize=16);
    plt.xlabel("Experimental conditions", fontsize=16);
    ax.set_xticklabels(order_names)
    plt.show()

# Stats

In [ ]:
column_names = ['marker', 'cond1', 'cond2', 'test_name', 'stat', 'pval', 'reject_stat', 
                'fdr_type', 'pval_fdr', 'reject_fdr']
df_stats = pd.DataFrame(columns = column_names)


test_pairs = [('cm3v', 'cm5v'), ('cm3v', 'vl3v'), ('cm3v', 'vl5v'), ('cm3v', 'anest'), 
            ('cm5v', 'vl3v'), ('cm5v', 'vl5v'), ('cm5v', 'anest'), 
            ('vl3v', 'vl5v'), ('vl3v', 'anest'), 
            ('vl5v', 'anest')]

fdr='fdr_bh'
test_name = 'stats.mannwhitneyu'

alpha = 0.05

for mark in df_all.marker.unique():
    print('Calculating marker : {}'.format(mark))
    df = df_all[df_all.marker == mark]        
    ps = []
    mstats = []
    stats_reject = []
    for pair in test_pairs:
        first  = df[df.stim_cond == pair[0]].avg_value
        second = df[df.stim_cond == pair[1]].avg_value
        stat, p = stats.mannwhitneyu(first, second, alternative='two-sided')
        print('Testing', pair[0], 'and', pair[1])
        print('\nStatistics=%.3f, p=%.3f' % (stat, p))
        ps.append(p)
        mstats.append(stat)
        # interpret
        if p > alpha:
            print('Same distribution (fail to reject H0).')
            stat_reject = False
        else:
            print('Different distribution (reject H0).')
            stat_reject = True
        stats_reject.append(stat_reject)

    # FDR correction
    rejected, p_val_corrected = statsmodels.stats.multitest.fdrcorrection(ps, alpha, method='indep')
    for i in range(len(test_pairs)):
        print('Testing', test_pairs[i][0], 'and', test_pairs[i][1])
        print('Rejected={}, p={}\n'.format(rejected[i], round(p_val_corrected[i],3)))

        df2 = pd.DataFrame([[mark, test_pairs[i][0], test_pairs[i][1], 
                             test_name, mstats[i], round(ps[i], 5), stats_reject[i], 
                             fdr, round(p_val_corrected[i], 5), rejected[i]                               
                            ]], columns = column_names)
        df_stats = df_stats.append(df2)

In [ ]:
df_stats

In [ ]:
df_stats.to_csv(path_or_buf='.../markers/stats.csv', index=False)

# Final figures
Only the significant paired tests are plotted. The results come from the stats above. 

## Figure 1

In [ ]:
colors = ["teal", "firebrick", "indianred", "slategray", "darkgray"]
classes_palette = sns.color_palette(colors)
sns.set_palette(classes_palette)


order = ['anest', 'cm3v', 'cm5v', 'vl3v', 'vl5v']
order_names = ['Anesthesia', 
               'Anesthesia + \n low CT-DBS', 'Anesthesia + \n high CT-DBS',
               'Anesthesia + \n low VL-DBS', 'Anesthesia + \n high VL-DBS']  
    
mark = 'nice/marker/PowerSpectralDensity/summary_se'
test_pairs = [('cm3v', 'cm5v'), ('cm3v', 'vl3v'), ('cm3v', 'anest'), 
                ('cm5v', 'vl3v'), ('cm5v', 'vl5v'), ('cm5v', 'anest'), 
                ('vl3v', 'vl5v'), ('vl3v', 'anest'), 
                ('vl5v', 'anest')]
text_annot_custom = ["**", "****", "***",
                     "****", "**", "****", 
                     "****", "**", 
                     "***"]

print('Calculating marker : {}'.format(mark))
df = df_all[df_all.marker == mark]

f, ax = plt.subplots(figsize=(8, 6))
ax=pt.RainCloud(x = "stim_cond", y = "avg_value", data = df, palette = classes_palette, bw = 0.3,
                width_viol = .6, width_box = 0.1, ax = ax, orient = "v", 
                move = .2, point_size=5, alpha=0.90,
                order=order) 
ax.set(ylim=(0.85, 0.94)) 
plt.ylabel("Spectral Entropy (SE) [arbitrary units]", fontsize=16);
plt.xlabel(" ", fontsize=16);
ax.set_xticklabels(order_names, rotation=40, ha='right')

ax2, test_results = add_stat_annotation(ax, data=df, x="avg_value", y="stim_cond", order=order, 
                                box_pairs=test_pairs, 
                                text_annot_custom= text_annot_custom, 
                                comparisons_correction=None,
                                test='Mann-Whitney', text_format='star',fontsize=11,
                                loc='outside', verbose=2, 
                                line_offset_to_box=0.05, line_offset=0.01, line_height=0.02, text_offset=1);

sns.despine(bottom=True, left=True)

plt.savefig(r".../figures/SE.pdf", 
        bbox_inches='tight')

plt.show()


## Supplementary figures

In [ ]:
mark = 'nice/marker/PowerSpectralDensity/deltan'
test_pairs = [('cm3v', 'cm5v'), ('cm3v', 'vl3v'), ('cm3v', 'vl5v'), ('cm3v', 'anest'), 
                ('cm5v', 'vl3v'), ('cm5v', 'vl5v'), ('cm5v', 'anest'), 
                ('vl3v', 'vl5v'), ('vl3v', 'anest'), 
                ('vl5v', 'anest')]
text_annot_custom = ["****", "****", "**", "****", 
                     "****", "**", "****", 
                     "****", "**", 
                     "****"]

print('Calculating marker : {}'.format(mark))
df = df_all[df_all.marker == mark]

f, ax = plt.subplots(figsize=(8, 6))
ax=pt.RainCloud(x = "stim_cond", y = "avg_value", data = df, palette = classes_palette, bw = 0.3,
                width_viol = .6, width_box = 0.1, ax = ax, orient = "v", 
                move = .2, point_size=5, alpha=0.90,
                order=order) 
ax.set(ylim=(0.1, 0.6)) 
plt.ylabel("Normalized Delta Power [arbitrary units]", fontsize=16);
plt.xlabel(" ", fontsize=16);
ax.set_xticklabels(order_names, rotation=40, ha='right')

ax2, test_results = add_stat_annotation(ax, data=df, x="avg_value", y="stim_cond", order=order, 
                                box_pairs=test_pairs, 
                                text_annot_custom= text_annot_custom, 
                                comparisons_correction=None,
                                test='Mann-Whitney', text_format='star',fontsize=11,
                                loc='outside', verbose=2, 
                                line_offset_to_box=0.05, line_offset=0.01, line_height=0.02, text_offset=1);

sns.despine(bottom=True, left=True)

plt.savefig(r".../figures/deltan.pdf", 
        bbox_inches='tight')

plt.show()

In [ ]:
mark = 'nice/marker/PowerSpectralDensity/thetan'
test_pairs = [('cm3v', 'vl3v'),  
                ('cm5v', 'vl3v'), ('cm5v', 'vl5v'), ('cm5v', 'anest'), 
                ('vl3v', 'vl5v'),
                ('vl5v', 'anest')]
text_annot_custom = ["*",
                     "****", "*", "**", 
                     "****",
                     "*"]

print('Calculating marker : {}'.format(mark))
df = df_all[df_all.marker == mark]

f, ax = plt.subplots(figsize=(8, 6))
ax=pt.RainCloud(x = "stim_cond", y = "avg_value", data = df, palette = classes_palette, bw = 0.3,
                width_viol = .6, width_box = 0.1, ax = ax, orient = "v", 
                move = .2, point_size=5, alpha=0.90,
                order=order) 
ax.set(ylim=(0.14, 0.30)) 
plt.ylabel("Normalized Theta Power [a.u.]", fontsize=16);
plt.xlabel(" ", fontsize=16);
ax.set_xticklabels(order_names, rotation=40, ha='right')

ax2, test_results = add_stat_annotation(ax, data=df, x="avg_value", y="stim_cond", order=order, 
                                box_pairs=test_pairs, 
                                text_annot_custom= text_annot_custom, 
                                comparisons_correction=None,
                                test='Mann-Whitney', text_format='star',fontsize=11,
                                loc='outside', verbose=2, 
                                line_offset_to_box=0.05, line_offset=0.01, line_height=0.02, text_offset=1);

sns.despine(bottom=True, left=True)

plt.savefig(r".../figures/thetan.pdf", 
        bbox_inches='tight')

plt.show()

In [ ]:
mark = 'nice/marker/PowerSpectralDensity/alphan'
test_pairs = [('cm3v', 'vl3v'),  ('cm3v', 'anest'), 
                ('cm5v', 'vl3v'), ('cm5v', 'anest'), 
                ('vl3v', 'vl5v'),
                ('vl5v', 'anest')]
text_annot_custom = ["***", "*", 
                     "****", "***",
                     "****", 
                     "****"]

print('Calculating marker : {}'.format(mark))
df = df_all[df_all.marker == mark]

f, ax = plt.subplots(figsize=(8, 6))
ax=pt.RainCloud(x = "stim_cond", y = "avg_value", data = df, palette = classes_palette, bw = 0.3,
                width_viol = .6, width_box = 0.1, ax = ax, orient = "v", 
                move = .2, point_size=5, alpha=0.90,
                order=order) 
ax.set(ylim=(0.055, 0.26)) 
plt.ylabel("Normalized Alpha Power [a.u.]", fontsize=16);
plt.xlabel(" ", fontsize=16);
ax.set_xticklabels(order_names, rotation=40, ha='right')
plt.yticks(np.arange(0.07, 0.27, 0.02))

ax2, test_results = add_stat_annotation(ax, data=df, x="avg_value", y="stim_cond", order=order, 
                                box_pairs=test_pairs, 
                                text_annot_custom= text_annot_custom, 
                                comparisons_correction=None,
                                test='Mann-Whitney', text_format='star',fontsize=11,
                                loc='outside', verbose=2, 
                                line_offset_to_box=0.05, line_offset=0.01, line_height=0.02, text_offset=1);

sns.despine(bottom=True, left=True)

plt.savefig(r".../figures/alphan.pdf", 
        bbox_inches='tight')

plt.show()

In [ ]:
mark = 'nice/marker/PowerSpectralDensitySummary/summary_msf'
test_pairs = [('cm3v', 'cm5v'), ('cm3v', 'vl3v'), ('cm3v', 'anest'), 
                ('cm5v', 'vl3v'), ('cm5v', 'vl5v'), ('cm5v', 'anest'), 
                ('vl3v', 'vl5v'), ('vl3v', 'anest'), 
                ('vl5v', 'anest')]
text_annot_custom = ["*", "****", "*",
                     "****", "*", "****", 
                     "****", "**", 
                     "***"]

print('Calculating marker : {}'.format(mark))
df = df_all[df_all.marker == mark]

f, ax = plt.subplots(figsize=(8, 6))
ax=pt.RainCloud(x = "stim_cond", y = "avg_value", data = df, palette = classes_palette, bw = 0.3,
                width_viol = .6, width_box = 0.1, ax = ax, orient = "v", 
                move = .2, point_size=5, alpha=0.90,
                order=order) 

plt.ylabel("Median Power Frequency (MSF) [Hz]", fontsize=16);
plt.xlabel(" ", fontsize=16);
ax.set_xticklabels(order_names, rotation=40, ha='right')


ax2, test_results = add_stat_annotation(ax, data=df, x="avg_value", y="stim_cond", order=order, 
                                box_pairs=test_pairs, 
                                text_annot_custom= text_annot_custom, 
                                comparisons_correction=None,
                                test='Mann-Whitney', text_format='star',fontsize=11,
                                loc='outside', verbose=2, 
                                line_offset_to_box=0.05, line_offset=0.01, line_height=0.02, text_offset=1);

sns.despine(bottom=True, left=True)

plt.savefig(r".../figures/summary_msf.pdf", 
        bbox_inches='tight')

plt.show()